In [1]:
from tile_ids_around_stations import buffer_between_tile_ids_and_subway_station,netmob_data_FOLDER_PATH,PATH_iris

epsilon = 100
(gdf_stations,joined,result,maxi_nb_tile) = buffer_between_tile_ids_and_subway_station(epsilon,netmob_data_FOLDER_PATH,PATH_iris)

Maximum number of NetMob Cell associated to a subway station: 4


In [6]:
from build_netmob_data import get_information_from_path
import glob 
import os 
from os import listdir
import pandas as pd

def read_csv(path,result,columns,dic_time_series = {}):
    df = pd.read_csv(path, sep = ' ', names = columns).set_index(['tile_id'])
    # Loop through each station. Get associated usefull Tile-id
    for station_ind in range(len(result)):
        station = result['COD_TRG'][station_ind]
        ids = result.tile_id[station_ind]
        
        df_station = df.loc[ids]
        df_station = df_station.transpose()
        df_station.index = pd.to_datetime(df_station.index)
        df_station=df_station.sort_index()
        
        if station in dic_time_series.keys():
            dic_time_series[station] = pd.concat([dic_time_series[station],df_station])
        else:
            dic_time_series[station]= df_station
            
    return(dic_time_series)

def tackle_one_day(result,netmob_data_FOLDER_PATH,app,day,dic_time_series,assert_transfer_mode):
    txt_paths = sorted(glob.glob(os.path.join(f'{netmob_data_FOLDER_PATH}/{app}/{day}', "*.txt")))
    for path in txt_paths:
        transfer_mode,columns = get_information_from_path(path)
        if transfer_mode == assert_transfer_mode:
            date_str = '-'.join([day[4:6],day[6:],day[:4]])   # date_str : 'MM-DD-YYYY'
            columns = ['tile_id'] + [date_str +' '+ c for c in columns if c != 'tile_id']
            dic_time_series = read_csv(path,result,columns,dic_time_series)
    return(dic_time_series)
            
def tackle_all_days(result,netmob_data_FOLDER_PATH,folder_days,app,dic_time_series={},assert_transfer_mode='DL'):
    for k,day in enumerate(folder_days):  # day : 'YYYYMMDD'
        dic_time_series = tackle_one_day(result,netmob_data_FOLDER_PATH,app,day,dic_time_series,assert_transfer_mode)
    return(dic_time_series)

#apps = [app for app in listdir(netmob_data_FOLDER_PATH) if ((app != 'Lyon.geojson') and (not app.startswith('.'))) ]   # Avoid hidden folder and Lyon.geojson
apps = ['Google_Maps','Uber','Facebook','Instagram','WhatsApp','Deezer']
for app in apps: 
    print('App: ',app)
    folder_days = [day for day in listdir(f'{netmob_data_FOLDER_PATH}/{app}') if (not day.startswith('.')) ] 
    dic_time_series = tackle_all_days(result,netmob_data_FOLDER_PATH,folder_days,app,dic_time_series={},assert_transfer_mode='DL')
    break
    

App:  Google_Maps


In [7]:
from constants.paths import FILE_NAME,FOLDER_PATH
from constants.config import get_args
from utils.utilities_DL import match_period_coverage_with_netmob,get_small_ds,get_DataSet_and_invalid_dates

model_name = 'STGCN'
dataset_names = ['subway_in','netmob']
args = get_args(model_name,dataset_names)
coverage = match_period_coverage_with_netmob(FILE_NAME,dataset_names)
(coverage,args) = get_small_ds(False,coverage,args)  #small_ds = False

dataset,invalid_dates = get_DataSet_and_invalid_dates(args.W,args.D,args.H,args.step_ahead,
                                                    single_station = False,coverage_period = coverage)

Time-step per hour: 4.0
coverage period: 2019-03-16 00:00:00 - 2019-05-31 23:45:00


In [8]:
from plotting.TS_analysis import plot_subway_patterns,drag_selection_box
from preprocess_subway_15 import get_trigram_correspondance
from bokeh.palettes import Turbo256 as palette
from bokeh.plotting import show,output_notebook,save,output_file
from bokeh.layouts import column

df_correspondance = get_trigram_correspondance()

Metro_A_stations = ['Ampère Victor Hugo', 'Bellecour', 'Charpennes',
       'Cordeliers', 'Cusset','Flachet', 'Foch','Gratte Ciel', 'Hôtel de ville - Louis Pradel',
       'La soie', 'Laurent Bonnevay','Masséna', 'Perrache', 'République Villeurbanne']
Metro_A_TRG = list(df_correspondance.set_index('Station').loc[Metro_A_stations].values.reshape(-1))
df_NetMob_consumption = pd.DataFrame({station: dic_time_series[station].mean(axis=1).sort_index() for station in Metro_A_TRG})
df_NetMob_consumption = df_NetMob_consumption.rename(columns = {Metro_A_TRG[k]:Metro_A_stations[k] for k in range(len(Metro_A_stations))})
width=1500
height=400
p1 = plot_subway_patterns(dataset.df,Metro_A_stations,palette,width,height,title=f'Trafic Volume by stations')
p2 = plot_subway_patterns(df_NetMob_consumption,Metro_A_stations,palette,width,height,title = f'Google-Maps Volume around stations ({epsilon}m)')
select = drag_selection_box(dataset.df,p1,p2,width=width,height=height//3)
output_notebook()
grid = column(p1,p2,select)
show(grid)

output_notebook()

if False: 
    output_file(filename=f"Google_Maps_consumption_{epsilon}m_around_stations.html")
    save(grid)
#show(p)

Loading BokehJS ...

Loading BokehJS ...

NameError: name 'p' is not defined